In [93]:
from elasticsearch import Elasticsearch
from itertools import groupby
from matplotlib import pyplot as plt
from tqdm import tqdm_notebook as tqdm
from influxdb import DataFrameClient
import datetime
import time
import pickle
import pandas as pd
import numpy as np
import pandas as pd
np.set_printoptions(suppress=True)
pd.set_option('display.float_format', lambda x: '%.0f' % x) #避免科学技术法
%matplotlib inline

# 时间转换

In [97]:
# '2015-08-28 16:43:37.283' --> 1440751417.283
# 或者 '2015-08-28 16:43:37' --> 1440751417.0
def string2timestamp(strValue):
 
    try:        
        d = datetime.datetime.strptime(strValue, "%Y-%m-%d %H:%M:%S.%f")
        t = d.timetuple()
        timeStamp = int(time.mktime(t))
        timeStamp = float(str(timeStamp) + str("%06d" % d.microsecond))/1000000
        print (timeStamp)
        return timeStamp
    except ValueError as e:
        print (e)
        d = datetime.datetime.strptime(str2, "%Y-%m-%d %H:%M:%S")
        t = d.timetuple()
        timeStamp = int(time.mktime(t))
        timeStamp = float(str(timeStamp) + str("%06d" % d.microsecond))/1000000
        print (timeStamp)
        return timeStamp
def timestamp2string(timeStamp):
    try:
        d = datetime.datetime.fromtimestamp(timeStamp)
        str1 = d.strftime("%Y-%m-%d %H:%M:%S.%f")
        # 2015-08-28 16:43:37.283000'
        return str1
    except Exception as e:
        print (e)
        return ''
now_str = datetime.datetime.now() 
#print(now_str)
now_timestamp=now_str.timestamp()
#print(now_timestamp)

#print(timestamp2string(1567055400))
#string2timestamp('2019-08-29 13:10:00.000000')

In [125]:
es_time_trans        =  10**6. #es的timestamp_millis查找比转换结果多3位
influxdb_time_trans = 10**9. #influxdb的timestamp查找比转换结果多9位
es_start         = string2timestamp('2019-08-29 21:10:00.000000') * es_time_trans
es_end          = string2timestamp('2019-08-29 21:25:00.000000') * es_time_trans
influxdb_start = int(string2timestamp('2019-08-29 13:10:00.000000') * influxdb_time_trans)  #influxdb是UTC时间,int避免科学技术
influxdb_end  = int(string2timestamp('2019-08-29 13:25:00.000000') * influxdb_time_trans)

1567084200.0
1567085100.0
1567055400.0
1567056300.0


# 导入ES数据

In [134]:
def search_all(index, body):
    rsp = es.search(index=index, body=dict(**body, size=1000), scroll='1m',request_timeout=30)
    total = rsp['hits']['total']
    print(total)
    scroll_id = rsp['_scroll_id']
    scroll_size = total
    with tqdm(total=total) as pbar:
        rets = []
        while scroll_size > 0:
            _rsp = es.scroll(scroll_id=scroll_id, scroll='1m')
            scroll_id = _rsp['_scroll_id']
            scroll_size = len(_rsp['hits']['hits'])
            total -= scroll_size
            rets.extend(parse(_rsp['hits']['hits']))
            pbar.update(scroll_size)        
    return rets


def parse(response):
    try:
        return list(map(
            lambda x: {
                'trace_id': x['_source']['traceId'],
                'timestamp': x['_source']['timestamp'],
                'latency': x['_source']['duration'],
                'http_status': x['_source']['tags']['http.status_code'],
                'request_parent_id': x['_source']['parentId'] if 'parentId' in x['_source'] else 'None',
                'request_id': x['_source']['id'],
                'source': x['_source']['localEndpoint']['serviceName'],
                'http_name': x['_source']['name'],
                'target': x['_source']['name'].split('.')[0] + '.default'
            },
            response,
        ))
    except KeyError:
        print('error:', response)

        
def dump_index(index):
    path = './event_title.txt'
    rets = search_all(
            index=index, 
            body={
                  "query": {
                    "range": {
                      "timestamp": {
                        "gte": es_start,
                        "lte" : es_end
                      }
                    }
                  }
                },
        
    )
    dump_path(path,rets)
    return rets

def dump_path(path,data):
    with open(path, 'wb+') as f:
        pickle.dump(data, f)

def load_path(path):
    with open(path, 'rb') as f:
        return pickle.load(f)


In [101]:
es = Elasticsearch(host='192.168.115.84', port=9200)
requests_8_29 = dump_index("zipkin:span-2019-08-29")
data_8_29=load_path('./event_title.txt')

40748


In [102]:
df = pd.DataFrame(data_8_29, columns=['trace_id',
                                      'timestamp',
                                      'latency',
                                      'http_status',
                                      'request_parent_id',
                                      'request_id',
                                      'source',
                                      'http_name',
                                      'target'] )
#df.to_csv('./event_title.csv')
df = df.drop(columns=['request_parent_id','request_id','http_name'])
df['source']=df['source'].apply(lambda x : ('.'+x).strip('default').strip('.'))
df['target']=df['target'].apply(lambda x : ('.'+x).strip('default').strip('.'))
df

trace_id         timestamp  latency  \
0      e5509cc13e65c4f7dd466bd545db0467  1567084431270215    38326   
1      3e4c92af33630580eca1ec210550f66f  1567084431776851     5079   
2      b6f73cac5f253f0776bc1bac01d4bbbe  1567084429493868     3861   
3      e5509cc13e65c4f7dd466bd545db0467  1567084431975592     4075   
4      e5509cc13e65c4f7dd466bd545db0467  1567084431969290     3123   
5      3e4c92af33630580eca1ec210550f66f  1567084432076206     4652   
6      e5509cc13e65c4f7dd466bd545db0467  1567084432376592     3982   
7      e5509cc13e65c4f7dd466bd545db0467  1567084429819328   134235   
8      3e4c92af33630580eca1ec210550f66f  1567084430470440     3949   
9      6d1bb6ea8133577502127e3401bbec41  1567084430288929     6962   
10     96cb5618c3137ac209dccc15a98f0fe4  1567084428344151     6871   
11     e5509cc13e65c4f7dd466bd545db0467  1567084430379987     2822   
12     e5509cc13e65c4f7dd466bd545db0467  1567084430624504     3555   
13     e5509cc13e65c4f7dd466bd545db0467  1567084426687082  2204431   
14     094ac42cc35dc46b5cdf8558894cb4ba  1567084426399867  2455034   
15     6d1bb6ea8133577502127e3401bbec41  1567084429023205   430160   
16     3f0dcfe6241923a3c2e73d660d200bb3  1567084446277954     5721   
17     db84fb2f835988b25034b1d716e5694b  1567084446170308     4832   
18     3f0dcfe6241923a3c2e73d660d200bb3  1567084446271486     4548   
19     db84fb2f835988b25034b1d716e5694b  1567084446376677     4846   
20     db84fb2f835988b25034b1d716e5694b  1567084446282609   293737   
21     3f0dcfe6241923a3c2e73d660d200bb3  1567084446575592     5891   
22     3f0dcfe6241923a3c2e73d660d200bb3  1567084446675779     5856   
23     db84fb2f835988b25034b1d716e5694b  1567084446016252     6187   
24     3b9f3b0b0cf03b86101522ed84457bdc  1567084446687665     5367   
25     db84fb2f835988b25034b1d716e5694b  1567084446875841     5255   
26     3f0dcfe6241923a3c2e73d660d200bb3  1567084446975588    30763   
27     2535a1e5dc7155f0eecf0ea287e89ccd  1567084442126175     6228   
28     2535a1e5dc7155f0eecf0ea287e89ccd  1567084442157808    49951   
29     3f0dcfe6241923a3c2e73d660d200bb3  1567084447191149     4761   
...                                 ...               ...      ...   
39718  d60e553d09bd38aaf8b60102d976e8c3  1567085051873352     2378   
39719  655dd34e111667b1e37f851215df1c53  1567085048306199     4724   
39720  6ee448440dbb5d97b9b8ef640f27d295  1567085049051950     3555   
39721  3539aa139499d651aa609098e91e5ed9  1567085051035701   689644   
39722  0c0d87b41fa039f47b0b17ca6c5c4993  1567085053107838     3889   
39723  b2f2b566fd2463cac6ab513e9530437e  1567085047305826  1987390   
39724  48f36477029b4c3d43b8ea3eb5603141  1567085051040640     5586   
39725  48f36477029b4c3d43b8ea3eb5603141  1567085051057717     5132   
39726  b6679e0616ab52ee786a3f8db0700f33  1567085049524278     2942   
39727  48f36477029b4c3d43b8ea3eb5603141  1567085050356013    51140   
39728  ba038e06677b382513d7c34d3c2d5e8b  1567085051402689     8105   
39729  48f36477029b4c3d43b8ea3eb5603141  1567085051075556     4235   
39730  b2f2b566fd2463cac6ab513e9530437e  1567085048775387     7649   
39731  4d263d0ab5d6da99150182644613986a  1567085053518081   101751   
39732  48f36477029b4c3d43b8ea3eb5603141  1567085051159412    11542   
39733  6e6703362aa78fa007eb86ed63c6aa64  1567085053851276     5324   
39734  6e6703362aa78fa007eb86ed63c6aa64  1567085053769080     4024   
39735  6e6703362aa78fa007eb86ed63c6aa64  1567085053767964     5420   
39736  6e6703362aa78fa007eb86ed63c6aa64  1567085053920083    79615   
39737  48f36477029b4c3d43b8ea3eb5603141  1567085050581718    11956   
39738  3539aa139499d651aa609098e91e5ed9  1567085051073788   688082   
39739  f7c5c0aa4f0f7623f1b83c5c361a50e3  1567085053507536   110653   
39740  6e6703362aa78fa007eb86ed63c6aa64  1567085053744848     3222   
39741  6e6703362aa78fa007eb86ed63c6aa64  1567085053951432     3467   
39742  6e6703362aa78fa007eb86ed63c6aa64  1567085054131037     4358   
39743  80b56225005ff301b68d7c69841fd262  

# 获取influxdb的数据

In [117]:
#> SELECT * FROM "h2o_feet" WHERE time >= '2015-08-17T23:48:00Z' AND time <= '2015-08-18T00:30:00Z'
#print('数据库中的名称'+str(client.get_list_database()))
#print('数据库中的表'+str(client.query('show measurements;')))

In [126]:
def get_db(svc):
    client = DataFrameClient('192.168.115.31',34002,'root','','aiops_metric')#初始化
    query = f'select * from "{svc}" where time >= {influxdb_start} and time<= {influxdb_end}'#time>now()-1h;
    result = dict(client.query(query,chunked=False))
    result = result[svc].reset_index().rename(columns={'index':'timestamp'})
    result['timestamp'] = result.apply(lambda x : x['timestamp'].timestamp(),axis=1)
    result['service'] = svc
    result['timestamp'] = result['timestamp']+28800 #8h的时差
    return result


#因为容器数目不一致，需要转换名称
def dflist_2_dblist(df):
    db_list=[]
    df_list=list(set(df['target']))
    for i in df_list:
        db_list.append('metric.'+i)
    return db_list


#读取fluxdb所有需要的数据为一个大表
def all_db(df):
    db_list=dflist_2_dblist(df)
    df=get_db(db_list[0])
    for i in db_list[1:]:
        df = pd.concat((df, get_db(i)))
    df['service']=df['service'].apply(lambda x:(x+'.').strip('metric').strip('.'))
    df = df.fillna(0)
    #cpu使用率，service，timestamp，内存使用率，内存使用量，文件系统写入速率，文件系统读取速率，网络发送速率，网络接受速率
    df.columns = ['cpu_use', 'target', 'timestamp', 'mem_use_percent', 'mem_use_amount', 
                         'file_write_rate',  'file_read_rate', 'net_send_rate', 'file_recieve_rate']
    return df

In [141]:
db_data = all_db(df)
db_data

/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:27: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



cpu_use                     target  timestamp  mem_use_percent  \
0        21          ts-travel-service 1567084200                0   
1        24          ts-travel-service 1567084260                0   
2        29          ts-travel-service 1567084320                0   
3        27          ts-travel-service 1567084380                0   
4        21          ts-travel-service 1567084440                0   
5        28          ts-travel-service 1567084500                0   
6        27          ts-travel-service 1567084560                0   
7        27          ts-travel-service 1567084620                0   
8        26          ts-travel-service 1567084680                0   
9        25          ts-travel-service 1567084740                0   
10       27          ts-travel-service 1567084800                0   
11       28          ts-travel-service 1567084860                0   
12       28          ts-travel-service 1567084920                0   
13       28          ts-travel-service 1567084980                0   
14       28          ts-travel-service 1567085040                0   
15       27          ts-travel-service 1567085100                0   
0        22           ts-basic-service 1567084200                0   
1        29           ts-basic-service 1567084260                0   
2        34           ts-basic-service 1567084320                0   
3        32           ts-basic-service 1567084380                0   
4        30           ts-basic-service 1567084440                0   
5        33           ts-basic-service 1567084500                0   
6        34           ts-basic-service 1567084560                0   
7        32           ts-basic-service 1567084620                0   
8        31           ts-basic-service 1567084680                0   
9        29           ts-basic-service 1567084740                0   
10       34           ts-basic-service 1567084800                0   
11       34           ts-basic-service 1567084860                0   
12       36           ts-basic-service 1567084920                0   
13       30           ts-basic-service 1567084980                0   
..      ...                        ...        ...              ...   
2         3          ts-cancel-service 1567084320                0   
3         3          ts-cancel-service 1567084380                0   
4         2          ts-cancel-service 1567084440                0   
5         3          ts-cancel-service 1567084500                0   
6         3          ts-cancel-service 1567084560                0   
7         2          ts-cancel-service 1567084620                0   
8         2          ts-cancel-service 1567084680                0   
9         2          ts-cancel-service 1567084740                0   
10        2          ts-cancel-service 1567084800                0   
11        2          ts-cancel-service 1567084860                0   
12        3          ts-cancel-service 1567084920                0   
13        3          ts-cancel-service 1567084980                0   
14        2          ts-cancel-service 1567085040                0   
15        2          ts-cancel-service 1567085100                0   
0         1  ts-preserve-other-service 1567084200                0   
1         1  ts-preserve-other-service 1567084260                0   
2         1  ts-preserve-other-service 1567084320                0   
3         1  ts-preserve-other-service 1567084380                0   
4         1  ts-preserve-other-service 1567084440                0   
5         1  ts-preserve-other-service 1567084500                0   
6         2  ts-preserve-other-service 1567084560                0   
7         1  ts-preserve-other-service 1567084620                0   
8         1  ts-preserve-other-service 1567084680                0   
9         1  ts-preserve-other-service 1567084740                0   
10        3  ts-preserve-other-service 1567084800                0   
11        2  t

# 整合

In [129]:
def time_to_little(data):
    n = (data - es_start ) // 60000000  
    return es_start/1000000 + n * 60

def es_time_to_little(df):
    df['timestamp'] = df['timestamp'].apply(time_to_little)#利用字典取分段函数
    df = df[~df['source'].isin(['istio-ingressgateway'])]
    return df

def zhenghe(df,db_data):
    df1 = df.copy()
    es_z = es_time_to_little(df1)
    result = pd.merge(es_z, db_data, on=['timestamp','target'])
    result['timestamp'] = df['timestamp']
    return result

In [130]:
zh=zhenghe(df,db_data)
zh

trace_id         timestamp  latency  \
0      e5509cc13e65c4f7dd466bd545db0467  1567084431270215    38326   
1      3e4c92af33630580eca1ec210550f66f  1567084431776851     5079   
2      e5509cc13e65c4f7dd466bd545db0467  1567084429493868     4075   
3      e5509cc13e65c4f7dd466bd545db0467  1567084431975592     3123   
4      e5509cc13e65c4f7dd466bd545db0467  1567084431969290     3982   
5      3e4c92af33630580eca1ec210550f66f  1567084432076206     3949   
6      e5509cc13e65c4f7dd466bd545db0467  1567084432376592     2822   
7      e53b248f8cb3374fadee96f3bca254e1  1567084429819328     7351   
8      89a7ff1bbd0281b4460d9e2e27e47838  1567084430470440     3192   
9      89a7ff1bbd0281b4460d9e2e27e47838  1567084430288929     3116   
10     b30643a599a3129c86d096a55dd62999  1567084428344151     2895   
11     89a7ff1bbd0281b4460d9e2e27e47838  1567084430379987     3067   
12     b30643a599a3129c86d096a55dd62999  1567084430624504     3234   
13     b30643a599a3129c86d096a55dd62999  1567084426687082     4778   
14     b30643a599a3129c86d096a55dd62999  1567084426399867     3622   
15     89a7ff1bbd0281b4460d9e2e27e47838  1567084429023205     2838   
16     b30643a599a3129c86d096a55dd62999  1567084446277954     3332   
17     89a7ff1bbd0281b4460d9e2e27e47838  1567084446170308     5012   
18     b30643a599a3129c86d096a55dd62999  1567084446271486     4306   
19     89a7ff1bbd0281b4460d9e2e27e47838  1567084446376677     4327   
20     89a7ff1bbd0281b4460d9e2e27e47838  1567084446282609     4144   
21     89a7ff1bbd0281b4460d9e2e27e47838  1567084446575592     3220   
22     1e3daacf1e7890561544078fb18a23e5  1567084446675779    13208   
23     89a7ff1bbd0281b4460d9e2e27e47838  1567084446016252     9354   
24     89a7ff1bbd0281b4460d9e2e27e47838  1567084446687665     3072   
25     89a7ff1bbd0281b4460d9e2e27e47838  1567084446875841     3052   
26     efa82c8331b951f3432686b4815d59c9  1567084446975588     3022   
27     89a7ff1bbd0281b4460d9e2e27e47838  1567084442126175     3248   
28     1d74db6b39ae169c20b32026a721bd8c  1567084442157808     4390   
29     094ac42cc35dc46b5cdf8558894cb4ba  1567084447191149     4733   
...                                 ...               ...      ...   
36803  c593546a0bcd0adfe321471dab061ba9  1567084929710676  1447484   
36804  c268dde598689f2a7456cbc3075e6d08  1567084924899531  1682478   
36805  ba526caded9a21817a34f775c1e5decb  1567084924710691   186802   
36806  70b283a59c0ba6159bc7c7080926fa69  1567084921492783    47859   
36807  36c2b5fa518420ff5c8ca40a55618896  1567084921984824    12794   
36808  b32979e4cfe8be7db9358cd5f9b10598  1567084924464527  2655270   
36809  6d956c68188940b733cdcbdc2ccb1ba4  1567084925355635  2017020   
36810  6cd4b4c83bdbdf65b5f9c5cd07b09519  1567084924643809  2265681   
36811  f4a4ff1bbb99d74493a1893e195891a3  1567084928672908  1555505   
36812  853226aa576a3cd635cefc8e7ed2e5ae  1567084929147597   677127   
36813  a653598c587f67aae9f3a7a573849fd3  1567084986477333   131143   
36814  51fcf06cae683490352c521c4a2ae157  1567084986624163   514613   
36815  8a292b5e5fe880b9330f53cad109214f  1567084981749072  7147073   
36816  045de2f539a07b420421b7cff8fea945  1567084986615812  5133336   
36817  6ba8db894bad92fae1341f540088d82c  1567084986624557   289679   
36818  03df33579fce307be646f46bd5964ef0  1567084986741385    51036   
36819  e5d9767a8c1db00872438a0267da7b8b  1567084985833307    19746   
36820  48964502e29f5a3e68e74ad4a378376d  1567084985791664    20959   
36821  aa18a1c0a51357b3393a1874ea68a7de  1567084986981853    38009   
36822  025673044ec7b2ead38b07638778f9f9  1567084986929176    22510   
36823  ee74b833d053cea0c0656e6c4cc9f147  1567084987008145    19064   
36824  02e049481ab7b3e92b34df49b65d4e60  1567084987045158  2009507   
36825  8853d61237c66937448f3855f9c9ba65  1567084986800739  3332802   
36826  95aaa9a3e72325cff9f20ffa042b6ade  1567084987210391    77811   
36827  4567acb25ef7f7cf34edeaeb3ce6e82c  1567084991664059    10743   
36828  6b5530899e12c00856b7190efc79c7cf  

# 转换为invocation

In [137]:
# 每个trace_id按照endtime降序进行排序，并转换为csv文件
#index需要咋csv中手动删除
def trans_csv(df):
    df['endtime']=df['timestamp']+df['latency']
    grouped = df.groupby('trace_id').apply(lambda x: x.sort_values('endtime', ascending=False))
    grouped['s_t']=grouped['source'].str.cat(grouped['target'],sep='->')
    grouped=grouped.drop(columns=['target','source','trace_id'])
    grouped.fillna(0)
    grouped.to_csv('grouped.csv') 
    #return grouped

#以traceid为单位进行整合
def trans(df):
    for i in df.columns[1:]:
        df[i]=str(list(df[i]))
    df=df.drop_duplicates(['trace_id'])
    return df

#得到按traceid整合后的invocation列表，没有error label
def trans_last(zh):
    trans_csv(zh)
    df=pd.read_csv('grouped.csv').drop(columns='Unnamed: 1')
    df1 = df.groupby('trace_id').apply(trans).drop(columns='trace_id')
    df1.to_csv('grouped1.csv')
    df2 = pd.read_csv('grouped1.csv').drop(columns='Unnamed: 1')
    return df2

#添加error的label
def error_label(error, df):
    outfile = df [ ( df['target'] == error ) & ( df['timestamp'] > es_start ) & (df['timestamp'] < es_end ) ] 
    error_traceid_set = set(outfile['trace_id'])
    return error_traceid_set
    
# 得到最终invo，es+指标+label，以字典格式保存在txt文件中
def dict_last(zh,path):
    dfn = trans_last(zh)
    error_traceid = error_label('ts-basic-service', df)
    dfn['label'] = dfn.trace_id.apply(lambda x: 1 if x in error_traceid else 0)
    dictn = dfn.to_dict(orient='records')
    dump_path(path,dictn)
    invo_dict=load_path(path)
    return invo_dict

In [138]:
invo_8_29 = dict_last(zh,'./invo_basic.txt')

In [139]:
invo_8_29

[{'trace_id': '00084bf4e31a5a323e2b69e8e2368ec6',
  'timestamp': '[1567084382490743, 1567084354687669, 1567084306925610]',
  'latency': '[12180, 5057, 6323]',
  'http_status': '[200, 200, 200]',
  'cpu_use': '[20.50201196070783, 30.90605216059944, 30.90605216059944]',
  'mem_use_percent': '[0.4042396545410156, 0.40468597412109375, 0.40468597412109375]',
  'mem_use_amount': '[999620608, 986808320, 986808320]',
  'file_write_rate': '[0.0, 0.0, 0.0]',
  'file_read_rate': '[0.0, 0.0, 0.0]',
  'net_send_rate': '[58651.99764598183, 103372.21845062985, 103372.21845062985]',
  'file_recieve_rate': '[43193.50901283812, 70098.86286490156, 70098.86286490156]',
  'endtime': '[1567084382502923, 1567084354692726, 1567084306931933]',
  's_t': "['ts-order-service->ts-order-service', 'ts-station-service->ts-station-service', 'ts-order-service->ts-station-service']",
  'label': 0},
 {'trace_id': '00340510346cd70a0ccc9d66eeff4443',
  'timestamp': '[1567084357717425]',
  'latency': '[2760]',
  'http_statu

In [140]:
load_path('./invo_basic.txt')

[{'trace_id': '00084bf4e31a5a323e2b69e8e2368ec6',
  'timestamp': '[1567084382490743, 1567084354687669, 1567084306925610]',
  'latency': '[12180, 5057, 6323]',
  'http_status': '[200, 200, 200]',
  'cpu_use': '[20.50201196070783, 30.90605216059944, 30.90605216059944]',
  'mem_use_percent': '[0.4042396545410156, 0.40468597412109375, 0.40468597412109375]',
  'mem_use_amount': '[999620608, 986808320, 986808320]',
  'file_write_rate': '[0.0, 0.0, 0.0]',
  'file_read_rate': '[0.0, 0.0, 0.0]',
  'net_send_rate': '[58651.99764598183, 103372.21845062985, 103372.21845062985]',
  'file_recieve_rate': '[43193.50901283812, 70098.86286490156, 70098.86286490156]',
  'endtime': '[1567084382502923, 1567084354692726, 1567084306931933]',
  's_t': "['ts-order-service->ts-order-service', 'ts-station-service->ts-station-service', 'ts-order-service->ts-station-service']",
  'label': 0},
 {'trace_id': '00340510346cd70a0ccc9d66eeff4443',
  'timestamp': '[1567084357717425]',
  'latency': '[2760]',
  'http_statu